In [1]:
import numpy as np
import pandas as pd
from sklearn.ensemble import RandomForestRegressor
from sklearn.metrics import mean_squared_error
from sklearn import svm
from sklearn.model_selection import cross_val_score
from statsmodels.tsa.ar_model import AutoReg
from sklearn.preprocessing import StandardScaler
from statsmodels.tsa.statespace.sarimax import SARIMAX
from tqdm import tqdm
import warnings
import matplotlib.pyplot as plt
from pmdarima.arima import auto_arima
import random
warnings.filterwarnings('ignore')

In [7]:
def to_dict(x, k1, k2):
    X_dict = {}
    for i in range(100):
        X_dict[i] = x[i*k1:(i+1)*k1, k2:]
    return X_dict

def convert(y1):
    k = y1[0].shape[0]
    y2 = np.zeros((100*k, 1))
    
    for i in range(100):
        for j in range(k):
            y2[k*i + j] = y1[i][j]
    return y2

def traintest_split(X, y):
    train_size = (4 * X.shape[0])//5
    test_size = (1 * X.shape[0])//5
    num_features = X.shape[1]

    X_train = np.zeros((train_size, num_features))
    X_test = np.zeros((test_size, num_features))
    y_train = np.zeros((train_size, 1))
    y_test = np.zeros((test_size, 1))
    test_counter = 0
    train_counter = 0

    for i in range(y.shape[0]):
        if i%150>=120:
            X_test[test_counter] = X[i]
            y_test[test_counter] = y[i]
            test_counter+=1
        else:
            X_train[train_counter] = X[i]
            y_train[train_counter] = y[i]
            train_counter+=1
    
    return X_train, y_train, X_test, y_test

def predict(X_train, y_train, X_test):
    predictions = {}
    for i in tqdm(range(100)):
        X = X_train[i]
        y = y_train[i]
        Xt = X_test[i]
        predictions[i] = np.zeros((Xt.shape[0], 1))

        for j in range(Xt.shape[0]):
            m = y.shape[0]
            model = SARIMAX(y, exog=X, order=(2, 1, 0), seasonal_order=(0, 0, 0, 0)) #order 211 or 210
            model_fit = model.fit(disp=True)
            prediction = model_fit.predict(m, m, exog=Xt[j])
            predictions[i][j] = prediction
            X = np.concatenate((X, Xt[j].reshape(1, X.shape[1])))
            y = np.concatenate((y, predictions[i][j].reshape(1, 1)))

    return predictions

def get_X(data):
    X_current_ratio = np.array(data["current_assets"]/data["current_liabilities"])
    X_current_ratio = X_current_ratio.reshape((X_current_ratio.shape[0],1))
    X_div_payout = np.array(data["dividend"]/data["net_income"])
    X_div_payout = X_div_payout.reshape((X_div_payout.shape[0],1))
    X_EPS = np.array(data["net_income"]/data["shares_outstanding"])
    X_EPS = X_div_payout.reshape((X_EPS.shape[0],1))
    X_DE = np.array(data["liabilities"]/data["equity"])
    X_DE = X_DE.reshape((X_DE.shape[0],1))

#     del data['net_income'] #imp
#     del data['shares_outstanding'] #imp
#     del data['liabilities'] #imp
#     del data['equity'] #imp
    for ind in data.index:
        data['Stock'][ind] = data['Stock'][ind][6:]
    
    X = data[['Stock', 'total_assets', 'current_assets', 'total_revenue', 'dividend', 'net_income', 'shares_outstanding', 'liabilities', 'equity']]
    X_date = np.array(data["Date"])
    
    X = np.array(X, dtype=float)

    X_month = np.zeros((X.shape[0],1))
    for i in range(len(X)):
        X_month[i]=X_date[i][5:7]
        
    
    
    X_combined = np.hstack([X, X_month, X_current_ratio, X_div_payout, X_DE]) #imp
    return X_combined

## Importing Data

In [8]:
train_data = pd.read_csv('Train.csv')
test_data = pd.read_csv('Test_x.csv')

y = train_data["price"].to_numpy()

y_train = y.reshape((y.shape[0], 1))
X_train = get_X(train_data)
X_test = get_X(test_data)

# X_train, y_train, X_test, y_test = traintest_split(X_train, y_train)

train_size = X_train.shape[0]//100
test_size = X_test.shape[0]//100

X_train = to_dict(X_train, train_size, 1)
y_train = to_dict(y_train, train_size, 0)
X_test = to_dict(X_test, test_size, 1)

## Prediction Models

### SARIMAX time series model (now auto_arima)

In [9]:
#011
predictions = predict(X_train, y_train, X_test)
y_pred = convert(predictions)

  0%|                                                   | 0/100 [00:00<?, ?it/s] This problem is unconstrained.

 Bad direction in the line search;
   refresh the lbfgs memory and restart the iteration.

 Line search cannot locate an adequate point after MAXLS
  function and gradient evaluations.
  Previous x, f and g restored.
 Possible causes: 1 error in function or gradient evaluation;
                  2 rounding error dominate computation.
 This problem is unconstrained.


RUNNING THE L-BFGS-B CODE

           * * *

Machine precision = 2.220D-16
 N =           15     M =           10

At X0         0 variables are exactly at the bounds

At iterate    0    f=  7.32751D-01    |proj g|=  8.47661D+04

At iterate    1    f=  7.32702D-01    |proj g|=  8.35095D+04

           * * *

Tit   = total number of iterations
Tnf   = total number of function evaluations
Tnint = total number of segments explored during Cauchy searches
Skip  = number of BFGS updates skipped
Nact  = number of active bounds at final generalized Cauchy point
Projg = norm of the final projected gradient
F     = final function value

           * * *

   N    Tit     Tnf  Tnint  Skip  Nact     Projg        F
   15      2     56      2     0     0   8.351D+04   7.327D-01
  F =  0.73270236109010889     

ABNORMAL_TERMINATION_IN_LNSRCH                              
RUNNING THE L-BFGS-B CODE

           * * *

Machine precision = 2.220D-16
 N =           15     M =           10

At X0         0 v


 Bad direction in the line search;
   refresh the lbfgs memory and restart the iteration.

 Line search cannot locate an adequate point after MAXLS
  function and gradient evaluations.
  Previous x, f and g restored.
 Possible causes: 1 error in function or gradient evaluation;
                  2 rounding error dominate computation.
 This problem is unconstrained.

 Bad direction in the line search;
   refresh the lbfgs memory and restart the iteration.

 Line search cannot locate an adequate point after MAXLS
  function and gradient evaluations.
  Previous x, f and g restored.
 Possible causes: 1 error in function or gradient evaluation;
                  2 rounding error dominate computation.
 This problem is unconstrained.



           * * *

Tit   = total number of iterations
Tnf   = total number of function evaluations
Tnint = total number of segments explored during Cauchy searches
Skip  = number of BFGS updates skipped
Nact  = number of active bounds at final generalized Cauchy point
Projg = norm of the final projected gradient
F     = final function value

           * * *

   N    Tit     Tnf  Tnint  Skip  Nact     Projg        F
   15      2     49      2     0     0   8.366D+04   7.276D-01
  F =  0.72763585530290720     

ABNORMAL_TERMINATION_IN_LNSRCH                              
RUNNING THE L-BFGS-B CODE

           * * *

Machine precision = 2.220D-16
 N =           15     M =           10

At X0         0 variables are exactly at the bounds

At iterate    0    f=  7.24515D-01    |proj g|=  8.68027D+04

At iterate    1    f=  7.24447D-01    |proj g|=  8.37347D+04

           * * *

Tit   = total number of iterations
Tnf   = total number of function evaluations
Tnint = total number of segments 


 Bad direction in the line search;
   refresh the lbfgs memory and restart the iteration.

 Line search cannot locate an adequate point after MAXLS
  function and gradient evaluations.
  Previous x, f and g restored.
 Possible causes: 1 error in function or gradient evaluation;
                  2 rounding error dominate computation.
 This problem is unconstrained.

 Bad direction in the line search;
   refresh the lbfgs memory and restart the iteration.

 Line search cannot locate an adequate point after MAXLS
  function and gradient evaluations.
  Previous x, f and g restored.
 Possible causes: 1 error in function or gradient evaluation;
                  2 rounding error dominate computation.
 This problem is unconstrained.


...


           * * *

Tit   = total number of iterations
Tnf   = total number of function evaluations
Tnint = total number of segments explored during Cauchy searches
Skip  = number of BFGS updates skipped
Nact  = number of active bounds at final generalized Cauchy point
Projg = norm of the final projected gradient
F     = final function value

           * * *

   N    Tit     Tnf  Tnint  Skip  Nact     Projg        F
   15      1     21      1     0     0   1.110D+05   5.704D-01
  F =  0.57037537602713695     

ABNORMAL_TERMINATION_IN_LNSRCH                              
RUNNING THE L-BFGS-B CODE

           * * *

Machine precision = 2.220D-16
 N =           15     M =           10

At X0         0 variables are exactly at the bounds

At iterate    0    f=  5.67742D-01    |proj g|=  1.11029D+05

           * * *

Tit   = total number of iterations
Tnf   = total number of function evaluations
Tnint = total number of segments explored during Cauchy searches
Skip  = number of BFGS updates


 Line search cannot locate an adequate point after MAXLS
  function and gradient evaluations.
  Previous x, f and g restored.
 Possible causes: 1 error in function or gradient evaluation;
                  2 rounding error dominate computation.
 This problem is unconstrained.

 Line search cannot locate an adequate point after MAXLS
  function and gradient evaluations.
  Previous x, f and g restored.
 Possible causes: 1 error in function or gradient evaluation;
                  2 rounding error dominate computation.
 This problem is unconstrained.

 Line search cannot locate an adequate point after MAXLS
  function and gradient evaluations.
  Previous x, f and g restored.
 Possible causes: 1 error in function or gradient evaluation;
                  2 rounding error dominate computation.
 This problem is unconstrained.



           * * *

Tit   = total number of iterations
Tnf   = total number of function evaluations
Tnint = total number of segments explored during Cauchy searches
Skip  = number of BFGS updates skipped
Nact  = number of active bounds at final generalized Cauchy point
Projg = norm of the final projected gradient
F     = final function value

           * * *

   N    Tit     Tnf  Tnint  Skip  Nact     Projg        F
   15      1     21      1     0     0   1.167D+05   5.599D-01
  F =  0.55992238753897960     

ABNORMAL_TERMINATION_IN_LNSRCH                              
RUNNING THE L-BFGS-B CODE

           * * *

Machine precision = 2.220D-16
 N =           15     M =           10

At X0         0 variables are exactly at the bounds

At iterate    0    f=  5.57343D-01    |proj g|=  1.18994D+05

           * * *

Tit   = total number of iterations
Tnf   = total number of function evaluations
Tnint = total number of segments explored during Cauchy searches
Skip  = number of BFGS updates


 Line search cannot locate an adequate point after MAXLS
  function and gradient evaluations.
  Previous x, f and g restored.
 Possible causes: 1 error in function or gradient evaluation;
                  2 rounding error dominate computation.
 This problem is unconstrained.

 Line search cannot locate an adequate point after MAXLS
  function and gradient evaluations.
  Previous x, f and g restored.
 Possible causes: 1 error in function or gradient evaluation;
                  2 rounding error dominate computation.
 This problem is unconstrained.

 Line search cannot locate an adequate point after MAXLS
  function and gradient evaluations.
  Previous x, f and g restored.
 Possible causes: 1 error in function or gradient evaluation;
                  2 rounding error dominate computation.
 This problem is unconstrained.

 Line search cannot locate an adequate point after MAXLS
  function and gradient evaluations.
  Previous x, f and g restored.
 Possible causes: 1 error in function o


           * * *

Tit   = total number of iterations
Tnf   = total number of function evaluations
Tnint = total number of segments explored during Cauchy searches
Skip  = number of BFGS updates skipped
Nact  = number of active bounds at final generalized Cauchy point
Projg = norm of the final projected gradient
F     = final function value

           * * *

   N    Tit     Tnf  Tnint  Skip  Nact     Projg        F
   15      1     21      1     0     0   1.197D+05   5.522D-01
  F =  0.55222289310019412     

ABNORMAL_TERMINATION_IN_LNSRCH                              
RUNNING THE L-BFGS-B CODE

           * * *

Machine precision = 2.220D-16
 N =           15     M =           10

At X0         0 variables are exactly at the bounds

At iterate    0    f=  5.49682D-01    |proj g|=  1.19808D+05

           * * *

Tit   = total number of iterations
Tnf   = total number of function evaluations
Tnint = total number of segments explored during Cauchy searches
Skip  = number of BFGS updates

In [6]:
import math
math.sqrt(mean_squared_error(y_test, y_pred))

NameError: name 'y_test' is not defined

In [ ]:
predictions = {}
for i in tqdm(range(100)):
    X = X_train[i]
    y = y_train[i]
    Xt = X_test[i]
    m = Xt.shape[0]

    step_wise=auto_arima(y.ravel(), exogenous= X, start_p=1, start_q=1, max_p=7, max_q=7, 
                     d=1, max_d=7, trace=False, error_action='ignore', suppress_warnings=True, 
                     stepwise=True)
    predictions[i] = step_wise.predict(n_periods=m, exogenous=Xt)

In [70]:
y_pred = convert(predictions)
mean_squared_error(y_test, y_pred)

23.710762052662194

In [74]:
#110
predictions = predict(X_train, y_train, X_test)
y_pred = convert(predictions)
mean_squared_error(y_test, y_pred)

100%|█████████████████████████████████████████| 100/100 [02:56<00:00,  1.76s/it]


20.815806062176357

### Random Forest

In [123]:
clf = RandomForestRegressor(n_estimators =10 , criterion='squared_error',max_depth=30, random_state=0)
clf.fit(X_train, y_train)
print(clf.score(X_train, y_train)*100)
# y_test = clf.predict(X_test_combined)

/var/folders/g3/cfqrmx7n2gg21yszg26kj02h0000gn/T/ipykernel_28932/678810325.py:2: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  clf.fit(X_train, y_train)


92.00668864321867


In [124]:
y_predict=clf.predict(X_train)
mean_squared_error(y_train, y_predict)

6.632265130117805

### SVM Regressor

In [125]:
clf_svm = svm.SVR(max_iter = 5000, degree =3)
clf_svm.fit(X_train, y_train)
print(clf.score(X_train, y_train)*100)

/opt/homebrew/Cellar/jupyterlab/3.6.1/libexec/lib/python3.11/site-packages/sklearn/utils/validation.py:1143: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


92.00668864321867


/opt/homebrew/Cellar/jupyterlab/3.6.1/libexec/lib/python3.11/site-packages/sklearn/svm/_base.py:299: ConvergenceWarning: Solver terminated early (max_iter=5000).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  warnings.warn(
